Example 1 - Number of DOF influence in Natural Frequency
=========
In this example, we use the rotor seen in Example 5.8.1 from {cite}`friswell2010dynamics`. Which is a symmetric rotor with a single disk in the center. The shaft is hollow with an outside diameter of $80 mm$, an inside
diameter of $30 mm$, and a length of $1.2 m$ and it is modeled using Euler-Bernoulli elements, with no internal shaft damping.
The bearings are rigid and short and the disk has a diameter of $400 mm$ and a thickness
of $80 mm$.
The disk and shaft elements are made of steel.

In [1]:
import numpy as np
import plotly.graph_objects as go
import ross as rs

import plotly.io as pio

pio.renderers.default = "notebook"

In [2]:
steel = rs.materials.steel

In [3]:
number_of_elements = [2, 4, 6, 8, 10, 12, 14, 16, 18, 20, 40, 60]

In [4]:
def create_rotor(n_el):
    """Create example rotor with given number of elements."""
    shaft = [
        rs.ShaftElement(1.2 / (n_el), idl=0.03, odl=0.08, material=steel)
        for i in range(n_el)
    ]

    disks = [
        rs.DiskElement.from_geometry(
            n=(n_el / 2), material=steel, width=0.08, i_d=0.08, o_d=0.4
        )
    ]

    bearings = [
        rs.BearingElement(0, kxx=1e15, cxx=0),
        rs.BearingElement(n_el, kxx=1e15, cxx=0),
    ]

    return rs.Rotor(shaft, disks, bearings)

In [5]:
def analysis(speed):
    """Perform convergence analysis for a given speed."""
    # create reference rotor with 80 elements
    n_eigen = 8
    rotor_80 = create_rotor(80)
    modal_80 = rotor_80.run_modal(speed, num_modes=2 * n_eigen)

    errors = np.zeros([len(number_of_elements), n_eigen])

    for i, n_el in enumerate(number_of_elements):
        rotor = create_rotor(n_el)
        modal = rotor.run_modal(speed, num_modes=2 * n_eigen)
        errors[i, :] = abs(
            100 * (modal.wn[:n_eigen] - modal_80.wn[:n_eigen]) / modal_80.wn[:n_eigen]
        )

    fig = go.Figure()
    for i in range(8):
        fig.add_trace(
            go.Scatter(x=number_of_elements, y=errors[:, i], name=f"Mode {i}")
        )
    fig.update_layout(
        xaxis=dict(title="Number of degrees of freedom"),
        yaxis=dict(type="log", title="Natural Frequency Error(%)"),
    )

    return fig

In [6]:
analysis(speed=0)

In [7]:
analysis(speed=5000 * np.pi / 30)

## References

```{bibliography}
:filter: docname in docnames
```